## Prerequisites

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import warnings
warnings.filterwarnings("ignore")

In [3]:
import numpy as np
import pandas as pd

from src.dataset.data import Dataset
from src.dataset.utils import negative_downsampling
from src.features.build_features import *
from src.features.process_fold import *
from src.model.train import *

import matplotlib.pyplot as plt
import seaborn as sns

pd.options.display.max_rows = 100
pd.options.display.max_columns = None

%matplotlib inline

In [8]:
from tsfresh import extract_features, extract_relevant_features
from tsfresh import select_features
from tsfresh.utilities.dataframe_functions import impute
from tsfresh.feature_extraction.settings import from_columns
from tsfresh.feature_extraction import ComprehensiveFCParameters, EfficientFCParameters, MinimalFCParameters

In [4]:
ds = Dataset()
ds.load_dataset()

In [5]:
build_uid(ds)

In [5]:
X = ds.X_train.reset_index()
y = ds.y_train.reset_index()['isFraud']
X_test = ds.X_test.reset_index()
X['isFraud'] = y

In [7]:
X.head(5)

TransactionID  TransactionDT  TransactionAmt ProductCD  card1  card2  \
0        2987000          86400            68.5         W  13926    NaN   
1        2987001          86401            29.0         W   2755  404.0   
2        2987002          86469            59.0         W   4663  490.0   
3        2987003          86499            50.0         W  18132  567.0   
4        2987004          86506            50.0         H   4497  514.0   

   card3       card4  card5   card6  addr1  addr2  dist1  dist2 P_emaildomain  \
0  150.0    discover  142.0  credit  315.0   87.0   19.0    NaN          None   
1  150.0  mastercard  102.0  credit  325.0   87.0    NaN    NaN     gmail.com   
2  150.0        visa  166.0   debit  330.0   87.0  287.0    NaN   outlook.com   
3  150.0  mastercard  117.0   debit  476.0   87.0    NaN    NaN     yahoo.com   
4  150.0  mastercard  102.0  credit  420.0   87.0    NaN    NaN     gmail.com   

  R_emaildomain   C1   C2   C3   C4   C5   C6   C7   C8   C9  C10  C11  C12  \
0          None  1.0  1.0  0.0  0.0  0.0  1.0  0.0  0.0  1.0  0.0  2.0  0.0   
1          None  1.0  1.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  1.0  0.0   
2          None  1.0  1.0  0.0  0.0  0.0  1.0  0.0  0.0  1.0  0.0  1.0  0.0   
3          None  2.0  5.0  0.0  0.0  0.0  4.0  0.0  0.0  1.0  0.0  1.0  0.0   
4          None  1.0  1.0  0.0  0.0  0.0  1.0  0.0  1.0  0.0  1.0  1.0  0.0   

    C13  C14     D1     D2    D3    D4   D5  D6  D7  D8  D9   D10    D11  D12  \
0   1.0  1.0   14.0    NaN  13.0   NaN  NaN NaN NaN NaN NaN  13.0   13.0  NaN   
1   1.0  1.0    0.0    NaN   NaN   0.0  NaN NaN NaN NaN NaN   0.0    NaN  NaN   
2   1.0  1.0    0.0    NaN   NaN   0.0  NaN NaN NaN NaN NaN   0.0  315.0  NaN   
3  25.0  1.0  112.0  112.0   0.0  94.0  0.0 NaN NaN NaN NaN  84.0    NaN  NaN   
4   1.0  1.0    0.0    NaN   NaN   NaN  NaN NaN NaN NaN NaN   NaN    NaN  NaN   

   D13  D14    D15    M1    M2    M3    M4    M5    M6    M7    M8    M9   V1  \
0  NaN  NaN    0.0     T     T     T    M2     F     T  None  None  None  1.0   
1  NaN  NaN    0.0  None  None  None    M0     T     T  None  None  None  NaN   
2  NaN  NaN  315.0     T     T     T    M0     F     F     F     F     F  1.0   
3  NaN  NaN  111.0  None  None  None    M0     T     F  None  None  None  NaN   
4  NaN  NaN    NaN  None  None  None  None  None  None  None  None  None  NaN   

    V2   V3   V4   V5   V6   V7   V8   V9  V10  V11  V12  V13  V14  V15  V16  \
0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  1.0  1.0  0.0  0.0   
1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  0.0  0.0  1.0  0.0  0.0   
2  1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  1.0  1.0  0.0  0.0   
3  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  1.0  1.0  1.0  0.0  0.0   
4  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   

   V17  V18  V19  V20  V21  V22  V23  V24  V25  V26  V27  V28  V29  V30  V31  \
0  0.0  0.0  1.0  1.0  0.0  0.0  1.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0   
1  0.0  0.0  1.0  1.0  0.0  0.0  1.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0   
2  0.0  0.0  1.0  1.0  0.0  0.0  1.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0   
3  0.0  0.0  1.0  1.0  0.0  0.0  1.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0   
4  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   

   V32  V33  V34  V35  V36  V37  V38  V39  V40  V41  V42  V43  V44  V45  V46  \
0  0.0  0.0  0.0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
1  0.0  0.0  0.0  0.0  0.0  1.0  1.0  0.0  0.0  1.0  0.0  0.0  1.0  1.0  1.0   
2  0.0  0.0  0.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  0.0  0.0  1.0  1.0  1.0   
3  0.0  0.0  0.0  1.0  1.0  1.0  1.0  0.0  0.0  1.0  0.0  0.0  1.0  1.0  1.0   
4  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   

   V47  V48  V49  V50  V51  V52  V53  V54  V55  V56  V57  V58  V59  V60  V61  \
0  NaN  NaN  NaN  NaN  NaN  NaN  1.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  1.0   
1  1.0  0.0  

In [9]:
X.shape

(590540, 441)

In [6]:
def group_fraud(X, col):
    fraud_card = X[[col, "isFraud"]].groupby(col).sum().reset_index()
    fraud_card.loc[fraud_card["isFraud"] > 0, "isFraud"] = 1 
    return fraud_card.set_index(col)

In [19]:
group_fraud(X, 'card1')['isFraud'].value_counts()

0.0    11813
1.0     1740
Name: isFraud, dtype: int64

In [24]:
group_fraud(X, 'uid')['isFraud'].value_counts()

0.0    12725
1.0     1799
Name: isFraud, dtype: int64

In [7]:
fraud_card_indexed = group_fraud(X, 'card1')

In [11]:
C_cols = ["C" + str(i) for i in range(1, 15)]
D_cols = ["D" + str(i) for i in range(1, 16)]

## tsfresh

Let's first analyze by `card1`

In [18]:
t_ = negative_downsampling(X, 0.1)

In [17]:
extracted_features = extract_features(X[C_cols + ['card1']].fillna(0), column_id="card1")

Feature Extraction: 100%|██████████████████████████████████████████████████████████████████████████| 10/10 [14:37<00:00, 87.76s/it]


In [21]:
extracted_features.head(10)

variable  C1__abs_energy  C1__absolute_sum_of_changes  \
id                                                      
1009                 4.0                          0.0   
1011                 9.0                          0.0   
1012                 2.0                          0.0   
1020                 1.0                          0.0   
1021                 1.0                          0.0   
1022                 1.0                          0.0   
1023                 1.0                          0.0   
1030              4918.0                        138.0   
1033                 1.0                          0.0   
1035                 1.0                          0.0   

variable  C1__agg_autocorrelation__f_agg_"mean"__maxlag_40  \
id                                                           
1009                                              0.000000   
1011                                              0.000000   
1012                                              0.000000   
1020                                              0.000000   
1021                                              0.000000   
1022                                              0.000000   
1023                                              0.000000   
1030                                             -0.180771   
1033                                              0.000000   
1035                                              0.000000   

variable  C1__agg_autocorrelation__f_agg_"median"__maxlag_40  \
id                                                             
1009                                               0.000000    
1011                                               0.000000    
1012                                               0.000000    
1020                                               0.000000    
1021                                               0.000000    
1022                                               0.000000    
1023                                               0.000000    
1030                                              -0.373057    
1033                                               0.000000    
1035                                               0.000000    

variable  C1__agg_autocorrelation__f_agg_"var"__maxlag_40  \
id                                                          
1009                                             0.000000   
1011                                             0.000000   
1012                                             0.000000   
1020                                             0.000000   
1021                                             0.000000   
1022                                             0.000000   
1023                                             0.000000   
1030                                             0.158138   
1033                                             0.000000   
1035                                             0.000000   

variable  C1__agg_linear_trend__f_agg_"max"__chunk_len_10__attr_"intercept"  \
id                                                                            
1009                                                    NaN                   
1011                                                    NaN                   
1012                                                    NaN                   
1020                                                    NaN                   
1021                                                    NaN                   
1022                                                    NaN                   
1023                                                    NaN                   
1030                                                    NaN                   
1033                                                    NaN                   
1035                                                    NaN                   

variable  C1__agg_linear_trend__f_agg_"max"__chunk_len_10__attr_"rvalue"  \
id                                         

In [24]:
extracted_features.shape

(4091, 2382)

In [23]:
fraud_card.shape

(4091, 2)

In [26]:
extracted_features_imputed = impute(extracted_features)

In [48]:
extracted_features_imputed.head(10)

variable  C1__abs_energy  C1__absolute_sum_of_changes  \
id                                                      
1009                 4.0                          0.0   
1011                 9.0                          0.0   
1012                 2.0                          0.0   
1020                 1.0                          0.0   
1021                 1.0                          0.0   
1022                 1.0                          0.0   
1023                 1.0                          0.0   
1030              4918.0                        138.0   
1033                 1.0                          0.0   
1035                 1.0                          0.0   

variable  C1__agg_autocorrelation__f_agg_"mean"__maxlag_40  \
id                                                           
1009                                              0.000000   
1011                                              0.000000   
1012                                              0.000000   
1020                                              0.000000   
1021                                              0.000000   
1022                                              0.000000   
1023                                              0.000000   
1030                                             -0.180771   
1033                                              0.000000   
1035                                              0.000000   

variable  C1__agg_autocorrelation__f_agg_"median"__maxlag_40  \
id                                                             
1009                                               0.000000    
1011                                               0.000000    
1012                                               0.000000    
1020                                               0.000000    
1021                                               0.000000    
1022                                               0.000000    
1023                                               0.000000    
1030                                              -0.373057    
1033                                               0.000000    
1035                                               0.000000    

variable  C1__agg_autocorrelation__f_agg_"var"__maxlag_40  \
id                                                          
1009                                             0.000000   
1011                                             0.000000   
1012                                             0.000000   
1020                                             0.000000   
1021                                             0.000000   
1022                                             0.000000   
1023                                             0.000000   
1030                                             0.158138   
1033                                             0.000000   
1035                                             0.000000   

variable  C1__agg_linear_trend__f_agg_"max"__chunk_len_10__attr_"intercept"  \
id                                                                            
1009                                              17.744048                   
1011                                              17.744048                   
1012                                              17.744048                   
1020                                              17.744048                   
1021                                              17.744048                   
1022                                              17.744048                   
1023                                              17.744048                   
1030                                              17.744048                   
1033                                              17.744048                   
1035                                              17.744048                   

variable  C1__agg_linear_trend__f_agg_"max"__chunk_len_10__attr_"rvalue"  \
id                                         

In [27]:
extracted_features_imputed.shape

(4091, 2382)

In [39]:
features_filtered = select_features(extracted_features_imputed, fraud_card_indexed['isFraud'])

In [41]:
features_filtered.shape

(4091, 981)

In [47]:
print(features_filtered.columns)

Index(['C2__number_peaks__n_5', 'C1__number_peaks__n_5',
       'C1__number_peaks__n_10', 'C2__number_peaks__n_10',
       'C2__number_peaks__n_3', 'C1__number_peaks__n_3',
       'C2__ratio_beyond_r_sigma__r_3',
       'C2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.8',
       'C2__energy_ratio_by_chunks__num_segments_10__segment_focus_9',
       'C1__ratio_beyond_r_sigma__r_3',
       ...
       'C3__fft_coefficient__coeff_76__attr_"real"',
       'C3__fft_coefficient__coeff_78__attr_"real"',
       'C3__fft_coefficient__coeff_79__attr_"angle"',
       'C3__fft_coefficient__coeff_79__attr_"imag"',
       'C3__fft_coefficient__coeff_74__attr_"real"',
       'C1__fft_coefficient__coeff_14__attr_"abs"',
       'C2__fft_coefficient__coeff_27__attr_"real"',
       'C2__fft_coefficient__coeff_27__attr_"abs"',
       'C1__fft_coefficient__coeff_27__attr_"real"',
       'C1__fft_coefficient__coeff_26__attr_"imag"'],
      dtype='object', name='variable', length=981)


Went from 4 features to almost 900, that's a lot, if we do that for counts, delays and V groups it's gonna be enormous

We should try and choose some relevant columns. From Boruta and other analysis, concentrate on Vgroups, M5, C1, C2, C6, C9, C11, C13, C14, D1, D2, D10, D15

## Custom FC 

https://tsfresh.readthedocs.io/en/latest/text/feature_extraction_settings.html#for-the-advanced-how-does-i-set-the-parameters-for-all-kind-of-time-series

In [60]:
settings = EfficientFCParameters()

In [56]:
features_filtered_direct = extract_relevant_features(
    X[C_cols + ['card1']].fillna(0), 
    fraud_card_indexed['isFraud'], 
    column_id="card1",
    default_fc_parameters=EfficientFCParameters()
)

Feature Extraction: 100%|██████████████████████████████████████████████████████████████████████████| 10/10 [10:30<00:00, 63.02s/it]


In [59]:
features_filtered_direct.head(15)

variable  C2__number_peaks__n_5  C1__number_peaks__n_5  \
id                                                       
1009                        0.0                    0.0   
1011                        0.0                    0.0   
1012                        0.0                    0.0   
1020                        0.0                    0.0   
1021                        0.0                    0.0   
1022                        0.0                    0.0   
1023                        0.0                    0.0   
1030                        0.0                    0.0   
1033                        0.0                    0.0   
1035                        0.0                    0.0   
1039                        1.0                    1.0   
1042                        0.0                    0.0   
1047                        0.0                    0.0   
1066                        0.0                    0.0   
1070                        0.0                    0.0   

variable  C1__number_peaks__n_10  C2__number_peaks__n_10  \
id                                                         
1009                         0.0                     0.0   
1011                         0.0                     0.0   
1012                         0.0                     0.0   
1020                         0.0                     0.0   
1021                         0.0                     0.0   
1022                         0.0                     0.0   
1023                         0.0                     0.0   
1030                         0.0                     0.0   
1033                         0.0                     0.0   
1035                         0.0                     0.0   
1039                         0.0                     0.0   
1042                         0.0                     0.0   
1047                         0.0                     0.0   
1066                         0.0                     0.0   
1070                         0.0                     0.0   

variable  C2__number_peaks__n_3  C1__number_peaks__n_3  \
id                                                       
1009                        0.0                    0.0   
1011                        0.0                    0.0   
1012                        0.0                    0.0   
1020                        0.0                    0.0   
1021                        0.0                    0.0   
1022                        0.0                    0.0   
1023                        0.0                    0.0   
1030                        0.0                    0.0   
1033                        0.0                    0.0   
1035                        0.0                    0.0   
1039                        1.0                    2.0   
1042                        0.0                    0.0   
1047                        0.0                    0.0   
1066                        0.0                    0.0   
1070                        0.0                    0.0   

variable  C2__ratio_beyond_r_sigma__r_3  \
id                                        
1009                           0.000000   
1011                           0.000000   
1012                           0.000000   
1020                           0.000000   
1021                           0.000000   
1022                           0.000000   
1023                           0.000000   
1030                           0.000000   
1033                           0.000000   
1035                           0.000000   
1039                           0.045455   
1042                           0.000000   
1047                           0.000000   
1066                           0.000000   
1070                           0.000000   

variable  C2__change_quantiles__f_agg_"var"__isabs_False__qh_1.0__ql_0.8  \
id                                                                         
1009                                                    0.0                
1011                                         

In [58]:
# extract columns that have been selected for future computations
from_columns(features_filtered_direct)

{'C2': {'number_peaks': [{'n': 5}, {'n': 10}, {'n': 3}, {'n': 1}, {'n': 50}],
  'ratio_beyond_r_sigma': [{'r': 3},
   {'r': 2.5},
   {'r': 2},
   {'r': 5},
   {'r': 6},
   {'r': 1.5},
   {'r': 7},
   {'r': 1},
   {'r': 10},
   {'r': 0.5}],
  'change_quantiles': [{'f_agg': 'var', 'isabs': False, 'qh': 1.0, 'ql': 0.8},
   {'f_agg': 'var', 'isabs': True, 'qh': 1.0, 'ql': 0.8},
   {'f_agg': 'mean', 'isabs': True, 'qh': 1.0, 'ql': 0.8},
   {'f_agg': 'var', 'isabs': True, 'qh': 1.0, 'ql': 0.6},
   {'f_agg': 'var', 'isabs': False, 'qh': 1.0, 'ql': 0.6},
   {'f_agg': 'var', 'isabs': True, 'qh': 1.0, 'ql': 0.4},
   {'f_agg': 'var', 'isabs': True, 'qh': 0.8, 'ql': 0.4},
   {'f_agg': 'mean', 'isabs': True, 'qh': 1.0, 'ql': 0.6},
   {'f_agg': 'var', 'isabs': False, 'qh': 1.0, 'ql': 0.4},
   {'f_agg': 'var', 'isabs': False, 'qh': 0.8, 'ql': 0.6},
   {'f_agg': 'var', 'isabs': True, 'qh': 0.8, 'ql': 0.6},
   {'f_agg': 'var', 'isabs': False, 'qh': 0.8, 'ql': 0.4},
   {'f_agg': 'mean', 'isabs': True, '

## Precalculate

Let's measure duration of computation

In [9]:
MinimalFCParameters()

{'sum_values': None,
 'median': None,
 'mean': None,
 'length': None,
 'standard_deviation': None,
 'variance': None,
 'maximum': None,
 'minimum': None}

In [ ]:
%%time
features_filtered_direct = extract_relevant_features(
    X[["C1", "C2", "C5", "C6", "C9", "C11", "C13", "C14", "D1", "D2", "D3", "D4", "D10", "D15"] + ['card1']].fillna(0), 
    fraud_card_indexed['isFraud'], 
    column_id="card1",
    default_fc_parameters=EfficientFCParameters()
)

Feature Extraction:  80%|████████████████████████████████████████████████████████▊              | 8/10 [2:37:19<35:56, 1078.25s/it]

In [ ]:
features_filtered_direct.to_csv("../../data/interim/tsfresh_features.csv")